In [1]:
# import files
import tensorflow as tf
import pandas as pd
import numpy as np
from nltk.corpus.reader.conll import ConllCorpusReader
import math
import collections
import random

In [2]:
# Read data from ConLL format file
root = './data/training'
word1 = './data/similarity/dev_x.csv'
word2 = './data/similarity/test_x.csv'
fileid = 'training-data.1m.conll'
columntypes = ['ignore', 'words', 'ignore', 'ignore', 'ignore','ignore','ignore','ignore','ignore','ignore']
corp = ConllCorpusReader(root, fileid, columntypes, encoding='utf8')

In [3]:
words = corp.words()

In [4]:
words = [word.encode('ascii','ignore')for word in words if word.encode('ascii','ignore').isalpha()]

In [5]:
# define vocabulary size
v_size = 160000

In [6]:
# lines1 = np.loadtxt(word1,delimiter=',',dtype='str')
# lines2 = np.loadtxt(word2,delimiter=',',dtype='str')
# lines1_col1 = lines1[1:,1]
# lines1_col2 = lines1[1:,2]
# l1 = np.concatenate((lines1_col1, lines1_col2))
# lines2_col1 = lines2[1:,1]
# lines2_col2 = lines2[1:,2]
# l2 = np.concatenate((lines2_col1, lines2_col2))
# need_to_keep = list(set().union(l1, l2))
# all_words = words + need_to_keep

In [24]:
lines1 = np.loadtxt(word1,delimiter=',',dtype='str')
lines2 = np.loadtxt(word2,delimiter=',',dtype='str')
lines1 = lines1[1:, 1:]
need_to_keep = list()
for l in lines1:
    need_to_keep.append(l[0])
    need_to_keep.append(l[1])
lines2 = lines2[1:, 1:]
for l in lines2:
    need_to_keep.append(l[0])
    need_to_keep.append(l[1])
all_words = words + need_to_keep

In [25]:
all_count = collections.Counter(all_words)
# dict_all = dict(collections.Counter(all_count))
dict1 = dict(collections.Counter(all_count).most_common(v_size))
dictionary = {'UNK' : 0}
dict1_keys = dict1.keys()
i = 1;
for key in dict1_keys:
    dictionary[key] = i
    i = i + 1

In [26]:
# all_count = collections.Counter(all_words)
# # dict_all = dict(collections.Counter(all_count))
# dict1 = dict(collections.Counter(all_count).most_common(v_size))
# dictionary = {'UNK' : 0}
# dict1_keys = dict1.keys()
# i = 1;
# for key in dict1_keys:
#     dictionary[key] = i
#     i = i + 1
to_keep = set(need_to_keep) - set(dict1_keys)
dict2 = {}
for i, each in enumerate(to_keep):
    dict2[each] = len(dictionary) + i + 1
dictionary.update(dict2)
reverse_dictionary = dict(zip(dictionary.values(), dictionary.keys()))
data = list()
for w in all_words:
    if w in dictionary:
        index = dictionary[w]
    else:
        index = 0
    data.append(index)

In [194]:
# #Build the dictionary and replace rare words with UNK token.
# def build_dataset(words):
    
#     count = [['UNK',-1]]
#     count.extend(collections.Counter(words).most_common(v_size-1))
#     dictionary = dict()
#     for word, _ in count:
#         dictionary[word] = len(dictionary)
#     data = list()
#     unk_count = 0
#     for word in words:
#         if word in dictionary:
#             index = dictionary[word]
#         else:
#             index = 0  # dictionary['UNK']
#             unk_count += 1
#         data.append(index)
#     count[0][1] = unk_count
#     reverse_dictionary = dict(zip(dictionary.values(), dictionary.keys()))
#     return data, count, dictionary, reverse_dictionary

In [224]:
# data, count, dictionary, reverse_dictionary = build_dataset(words)

In [190]:
# print('Most common words (+UNK)', count[:5])
# print('Sample data', data[:10], [reverse_dictionary[i] for i in data[:10]])

In [27]:
def generate_batch(batch_size, num_skips, skip_window):
    global data_index
    assert batch_size % num_skips == 0
    assert num_skips <= 2 * skip_window
    batch = np.ndarray(shape=(batch_size), dtype=np.int32)
    labels = np.ndarray(shape=(batch_size, 1), dtype=np.int32)
    span = 2 * skip_window + 1  # [ skip_window target skip_window ]
    buffer = collections.deque(maxlen=span)
    for _ in range(span):
        buffer.append(data[data_index])
        data_index = (data_index + 1) % len(data)
    for i in range(batch_size // num_skips):
        target = skip_window  # target label at the center of the buffer
        targets_to_avoid = [skip_window]
        for j in range(num_skips):
            while target in targets_to_avoid:
                target = random.randint(0, span - 1)
            targets_to_avoid.append(target)
            batch[i * num_skips + j] = buffer[skip_window]
            labels[i * num_skips + j, 0] = buffer[target]
        buffer.append(data[data_index])
        data_index = (data_index + 1) % len(data)
#Backtrack a little bit to avoid skipping words in the end of a batch
    data_index = (data_index + len(data) - span) % len(data)
    return batch, labels

In [28]:
data_index = 0

In [29]:
batch, labels = generate_batch(batch_size=8, num_skips=2, skip_window=1)
for i in range(8):
    print(batch[i], reverse_dictionary[batch[i]],
        '->', labels[i, 0], reverse_dictionary[labels[i, 0]])

(46380, 'Centers', '->', 29684, 'The')
(46380, 'Centers', '->', 106388, 'for')
(106388, 'for', '->', 67408, 'Disease')
(106388, 'for', '->', 46380, 'Centers')
(67408, 'Disease', '->', 146653, 'Control')
(67408, 'Disease', '->', 106388, 'for')
(146653, 'Control', '->', 67408, 'Disease')
(146653, 'Control', '->', 120839, 'and')


In [47]:
len(reverse_dictionary)
reverse_dictionary[160001]

KeyError: 160001

In [45]:
for i in range(160360):
    print i 
    print reverse_dictionary[i]

0
UNK
1
fawn
2
Keach
3
Tadier
4
Calland
5
Villalon
6
nunnery
7
Namoff
8
Xarelto
9
Berggruen
10
inadvertantly
11
gag
12
woods
13
clotted
14
spiders
15
Nampo
16
hanging
17
Nampa
18
woody
19
trawling
20
hastily
21
comically
22
localized
23
spidery
24
regularize
25
disobeying
26
canes
27
LAST
28
Deciphering
29
Septimus
30
Andiwal
31
Hughton
32
Eury
33
Fabros
34
Osawe
35
Lasry
36
nonfactor
37
Archuleta
38
refunding
39
caned
40
Western
41
Beinisch
42
crossbar
43
Gravesend
44
Bowhunters
45
rumbustious
46
Retreat
47
Euro
48
Wandzilak
49
Tempton
50
Hidrographical
51
touristed
52
Valli
53
Kirwan
54
Valle
55
Famed
56
Blade
57
avgas
58
pigment
59
Sderling
60
Mizell
61
Secularist
62
Larijani
63
PartyGaming
64
Morten
65
PORTLAND
66
bringing
67
seamier
68
Valls
69
lozenges
70
wooded
71
Saca
72
grueling
73
Pronk
74
wooden
75
wholemeal
76
Saco
77
Miers
78
Miert
79
Sergeants
80
Sack
81
ambushing
82
LOVEFiLM
83
chameleons
84
crotch
85
Zora
86
Sacr
87
Bayonetta
88
Miera
89
Malenchenko
90
Transitions
91
im

KeyError: 160001

In [32]:
# Step 4: Build and train a skip-gram model.

batch_size = 128
embedding_size = 200  # Dimension of the embedding vector.
skip_window = 5       # How many words to consider left and right.
num_skips = 4         # How many times to reuse an input to generate a label.

# We pick a random validation set to sample nearest neighbors. Here we limit the
# validation samples to the words that have a low numeric ID, which by
# construction are also the most frequent.
valid_size = 16     # Random set of words to evaluate similarity on.
valid_window = 100  # Only pick dev samples in the head of the distribution.
valid_examples = np.random.choice(valid_window, valid_size, replace=False)
num_sampled = 64    # Number of negative examples to sample.

In [33]:
graph = tf.Graph()
size = len(dictionary)
with graph.as_default():
# Input data.
    train_inputs = tf.placeholder(tf.int32, shape=[batch_size])
    train_labels = tf.placeholder(tf.int32, shape=[batch_size, 1])
    valid_dataset = tf.constant(valid_examples, dtype=tf.int32)
# Ops and variables pinned to the CPU because of missing GPU implementation
    with tf.device('/cpu:0'):
    # Look up embeddings for inputs.
        embeddings = tf.Variable(
            tf.random_uniform([size, embedding_size], -1.0, 1.0))
        embed = tf.nn.embedding_lookup(embeddings, train_inputs)

    # Construct the variables for the NCE loss
        nce_weights = tf.Variable(
        tf.truncated_normal([size, embedding_size],
                            stddev=1.0 / math.sqrt(embedding_size)))
        nce_biases = tf.Variable(tf.zeros([size]))

# Compute the average NCE loss for the batch.
# tf.nce_loss automatically draws a new sample of the negative labels each
# time we evaluate the loss.
    loss = tf.reduce_mean(
      tf.nn.nce_loss(weights=nce_weights,
                     biases=nce_biases,
                     labels=train_labels,
                     inputs=embed,
                     num_sampled=num_sampled,
                     num_classes=size))
    # Construct the SGD optimizer using a learning rate of 1.0.
    optimizer = tf.train.GradientDescentOptimizer(0.8).minimize(loss)
# Compute the cosine similarity between minibatch examples and all embeddings.
    norm = tf.sqrt(tf.reduce_sum(tf.square(embeddings), 1, keep_dims=True))
    normalized_embeddings = embeddings / norm
    valid_embeddings = tf.nn.embedding_lookup(
      normalized_embeddings, valid_dataset)
    similarity = tf.matmul(
      valid_embeddings, normalized_embeddings, transpose_b=True)
# Add variable initializer.
    init = tf.global_variables_initializer()


In [34]:
# Step 5: Begin training.
num_steps = 1000001

with tf.Session(graph=graph) as session:
    # We must initialize all variables before we use them.
    init.run()
    print("Initialized")

    average_loss = 0
    for step in xrange(num_steps):
        batch_inputs, batch_labels = generate_batch(
        batch_size, num_skips, skip_window)
        feed_dict = {train_inputs: batch_inputs, train_labels: batch_labels}

    # We perform one update step by evaluating the optimizer op (including it
    # in the list of returned values for session.run()
        _, loss_val = session.run([optimizer, loss], feed_dict=feed_dict)
        average_loss += loss_val

        if step % 2000 == 0:
            if step > 0:
                average_loss /= 2000
            # The average loss is an estimate of the loss over the last 2000 batches.
            print("Average loss at step ", step, ": ", average_loss)
            average_loss = 0

        # Note that this is expensive (~20% slowdown if computed every 500 steps)
    #     if step % 10000 == 0:
    #         sim = similarity.eval()
    #         for i in xrange(valid_size):
    #             valid_word = reverse_dictionary[valid_examples[i]]
    #             top_k = 8  # number of nearest neighbors
    #             nearest = (-sim[i, :]).argsort()[1:top_k + 1]
    #             log_str = "Nearest to %s:" % valid_word
    #             for k in xrange(top_k):
    #                 close_word = reverse_dictionary[nearest[k]]
    #                 log_str = "%s %s," % (log_str, close_word)
    #             print(log_str)
    final_embeddings = normalized_embeddings.eval()
    

Initialized
('Average loss at step ', 0, ': ', 333.83050537109375)
('Average loss at step ', 2000, ': ', 176.76459736442567)
('Average loss at step ', 4000, ': ', 111.07997948360443)
('Average loss at step ', 6000, ': ', 84.376164815425867)
('Average loss at step ', 8000, ': ', 69.64127140569687)
('Average loss at step ', 10000, ': ', 57.327318114101885)
('Average loss at step ', 12000, ': ', 48.626323482096197)
('Average loss at step ', 14000, ': ', 42.850031100779773)
('Average loss at step ', 16000, ': ', 38.222358324050902)
('Average loss at step ', 18000, ': ', 32.486464877873658)
('Average loss at step ', 20000, ': ', 29.206985041439534)
('Average loss at step ', 22000, ': ', 26.131403088897468)
('Average loss at step ', 24000, ': ', 23.737346467942)
('Average loss at step ', 26000, ': ', 21.473824027478695)
('Average loss at step ', 28000, ': ', 18.949513224393129)
('Average loss at step ', 30000, ': ', 17.63775692886114)
('Average loss at step ', 32000, ': ', 16.613774153783918

InvalidArgumentError: indices[104] = 160359 is not in [0, 160359)
	 [[Node: nce_loss/embedding_lookup_1 = Gather[Tindices=DT_INT64, Tparams=DT_FLOAT, _class=["loc:@Variable_2"], validate_indices=true, _device="/job:localhost/replica:0/task:0/cpu:0"](Variable_2/read, nce_loss/concat)]]

Caused by op u'nce_loss/embedding_lookup_1', defined at:
  File "/Users/MJ/anaconda/lib/python2.7/runpy.py", line 174, in _run_module_as_main
    "__main__", fname, loader, pkg_name)
  File "/Users/MJ/anaconda/lib/python2.7/runpy.py", line 72, in _run_code
    exec code in run_globals
  File "/Users/MJ/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py", line 3, in <module>
    app.launch_new_instance()
  File "/Users/MJ/anaconda/lib/python2.7/site-packages/traitlets/config/application.py", line 596, in launch_instance
    app.start()
  File "/Users/MJ/anaconda/lib/python2.7/site-packages/ipykernel/kernelapp.py", line 442, in start
    ioloop.IOLoop.instance().start()
  File "/Users/MJ/anaconda/l

In [259]:
final_embeddings.shape[0]

120661

In [24]:
type(reverse_dictionary.values())

list

In [191]:
dict1['dog']

KeyError: 'dog'

In [56]:
values = np.array(reverse_dictionary.values())

In [54]:
final_embeddings.shape

(150000, 200)

In [110]:
len(nums)

128

In [152]:
final_embeddings[1]

array([-0.11531205, -0.09879255, -0.146653  , -0.07100271, -0.04740517,
        0.02413479,  0.05497774, -0.03508486, -0.13806251, -0.01868239,
       -0.11635241, -0.06992918,  0.11057496, -0.06759588,  0.0711368 ,
       -0.11394672,  0.08112442, -0.09585679,  0.13774346,  0.06396436,
       -0.09375279,  0.13884579, -0.03244209, -0.11920168, -0.1135597 ,
        0.10370661, -0.12492667,  0.01526131, -0.10895998, -0.03710135,
        0.01080104, -0.09327574, -0.12912573,  0.0735561 ,  0.08278323,
       -0.11509752, -0.11647388, -0.09894896, -0.0238025 ,  0.04277151,
        0.12889758, -0.04803468,  0.03495275,  0.11272556,  0.02263451,
       -0.12159862, -0.11206925,  0.10393532, -0.00850879, -0.04926175,
       -0.06845825, -0.01461785,  0.0902633 , -0.11552854, -0.03705446,
       -0.0220232 ,  0.02758978,  0.13026102, -0.03313469, -0.04470359,
        0.12665319, -0.07617747, -0.09663025, -0.14645478, -0.15544055,
        0.03621043,  0.00785683,  0.07540513,  0.00995272,  0.07

In [252]:
np.dot(final_embeddings[dictionary['boy']], final_embeddings[dictionary['cash']])

0.2031437

In [253]:
with open('embed.txt', 'wb') as f:
    print final_embeddings.shape[0]
    for i in xrange(final_embeddings.shape[0]):
        if i % 1000 == 0:
            print i
        nums = str(final_embeddings[i])[1:-1].split()
        f.write(reverse_dictionary[i] + ' ' + ' '.join(nums) + '\n')
    f.write(reverse_dictionary[i] + )

120661
0
1000
2000
3000
4000
5000
6000
7000
8000
9000
10000
11000
12000
13000
14000
15000
16000
17000
18000
19000
20000
21000
22000
23000
24000
25000
26000
27000
28000
29000
30000
31000
32000
33000
34000
35000
36000
37000
38000
39000
40000
41000
42000
43000
44000
45000
46000
47000
48000
49000
50000
51000
52000
53000
54000
55000
56000
57000
58000
59000
60000
61000
62000
63000
64000
65000
66000
67000
68000
69000
70000
71000
72000
73000
74000
75000
76000
77000
78000
79000
80000
81000
82000
83000
84000
85000
86000
87000
88000
89000
90000
91000
92000
93000
94000
95000
96000
97000
98000
99000
100000
101000
102000
103000
104000
105000
106000
107000
108000
109000
110000
111000
112000
113000
114000
115000
116000
117000
118000
119000
120000


KeyError: 120660

In [260]:
f = './embed.txt'
ccc = len(open(f,'rU').readlines())
ccc

120660

In [35]:
np.savetxt("embeddings.txt",final_embeddings,delimiter=' ')

In [32]:
# Step 6: Visualize the embeddings.


def plot_with_labels(low_dim_embs, labels, filename='tsne.png'):
    assert low_dim_embs.shape[0] >= len(labels), "More labels than embeddings"
    plt.figure(figsize=(18, 18))  # in inches
    for i, label in enumerate(labels):
        x, y = low_dim_embs[i, :]
        plt.scatter(x, y)
        plt.annotate(label,
                 xy=(x, y),
                 xytext=(5, 2),
                 textcoords='offset points',
                 ha='right',
                 va='bottom')

    plt.savefig(filename)

try:
    from sklearn.manifold import TSNE
    import matplotlib.pyplot as plt

    tsne = TSNE(perplexity=30, n_components=2, init='pca', n_iter=5000)
    plot_only = 500
    low_dim_embs = tsne.fit_transform(final_embeddings[:plot_only, :])
    labels = [reverse_dictionary[i] for i in xrange(plot_only)]
    plot_with_labels(low_dim_embs, labels)

except ImportError:
    print("Please install sklearn, matplotlib, and scipy to visualize embeddings.")

ValueError: array must not contain infs or NaNs